In [1]:
from __future__ import print_function
import matplotlib.pyplot as plt # librairie de plot
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import numpy as np
import networkx as nx
import matplotlib.animation as animation

def un(x):
    return 1.0

# SEIR Model on graph

In the previous model we consider that the **spatial propagation** of the epidemy is homogeneous or **the population** are homogeneous. It is not the case in pratice.

To treat these different problems we propose to solve epidemic on **graph**. In this case each node is a SIR/SEIR models.

Applications:
- **Spatial propagation**: each node represent contry/city/discrit. There is exchange between the node. In this case **the travel**.
- **Inhomogeneous population**: community/familly, AIDS epidemic. We consider that, the dynamic is. Not the same inside some group of peoples and between the groups. In this case each node is group/comunity and the graph modelize interaction/mixing between the group.



In ihomogeneous population or spatial propagation the **parameters are not the same**. In general the main parameter which change is the **average number of contact by day**

Applications:
- **Spatial propagation**: The average number of contact depending of the density to the city/contry etc. More contact in Paris than Mulhouse.
- **Inhomogeneous population**: more contacts inside the group/community that with the exterior people. Different contact number between the community/group.

A first approach consist to separate the**dynamic inside the cities** (dense part) and **between the cities** which is slower since a small portion of the population travel each day.

For that the model proposed in *Diseases in metapopulations* of J. Aniro is to construct a comportemental model (SEIR here) on each node to a **oriented graph**. The models are coupled together by input/output fluxes of population which correspond to the **travels between the cities**.

## The model

We consider four functions by city $i$: susceptible peoples $S_i(t)$, exposed peoples $E_i(t)$ ,infectious peoples $I_i(t)$ and retired peoples $R_i(t)$. The dynamic is described by

\begin{align}
\dot{S}_i(t) & = -\beta \frac{S_i(t)I_i(t)}{N_i(t)} - g_1S_i(t) + g_1\sum_{j\in v(i)} m_{ji}S_j(t)  \\
\dot{E}_i(t) & = \beta \frac{S_i(t)I_i(t)}{N_i(t)} -\sigma E_i(t)- g_1E_i(t) + g_1\sum_{j\in v(i)} m_{ji}E_j(t) \\
\dot{I}_i(t) & = \sigma E(t) - \gamma I(t)  - g_2I_i(t) + g_2\sum_{j\in v(i)} I_j(t) \\
\dot{R}_i(t) & = \gamma I(t) - g_2 R_i(t) + g_2\sum_{j\in v(i)} R_j(t)
\end{align}

with $N_i(t)=S_i(t)+E_i(t)+I_i(t)+R_i(t)$ the total population, $g_1$ the proportion of the non symptomatic population which travel by day and $g_2$ the proportion of symptomatic population which travel by day.

To assure that all the peoples which leave a city go in another city we need:

$$
\sum_{j\in v(i)} m_{ji}=1
$$

with $v(i)$ the set of the node graph which are predecessor of $i$ node for the graph.

## Numerical scheme

We use the same numerical scheme as before. It is a **first order Lie Splitting** where we solve firstly each city before to solve the travel part. Each part is solve with a **forward Euler scheme**. 

In [2]:
class SEIR:
    
    def __init__(self,S0,E0):
        self.S = [S0]; self.E = [E0]  
        self.I = [0.0]; self.R = [0.0];  self.Rt = []
        self.N = [self.S[-1] +self.E[-1] + self.I[-1] +self.R[-1]]     
        self.k1=np.zeros(5,float)
        self.xn=np.zeros(5,float)
        self.xnp=np.zeros(5,float)
        
    def push_Rt(self,R0):
        self.Rt.append(R0*self.S[-1]/self.N[-1])
        
    def updateN(self):
        self.N[-1]=self.S[-1]+self.E[-1]+self.I[-1]+self.R[-1]
        
    def push_list_to_n(self):
        self.xn[0:5]=[self.S[-1],self.E[-1],self.I[-1],self.R[-1],self.N[-1]]
    
    def update(self,vp,v1,v2,dt,beta,sig,gamma):         
        vp[0] = v1[0]- dt*beta*v2[0]*v2[2]/v2[4] 
        vp[1] = v1[1]+ dt*beta*v2[0]*v2[2]/v2[4] - dt*sig*v2[1]
        vp[2] = v1[2]+ dt*sig*v2[1] -dt*gamma*v2[2]
        vp[3] = v1[3]+ dt*gamma*v2[2]  
        vp[4] = vp[0]+vp[1]+vp[2]+vp[3]
        
    def push_np_to_list(self):     
        self.S.append(self.xnp[0]);  self.E.append(self.xnp[1]);  
        self.I.append(self.xnp[2]);  self.R.append(self.xnp[3]);  
        self.N.append(self.xnp[4])

In [3]:
def construct_graph(S0,E0):
    villes = nx.DiGraph()
    villes.nodes.data()
    epi_paris = SEIR(0.35*int(S0),0.0)
    villes.add_node(1, name="Paris", epi=epi_paris, cut=1.0)
    
    epi_marseille = SEIR(0.15*int(S0),0.0)
    villes.add_node(2, name="Marseille", epi=epi_marseille, cut=1.0)
    
    epi_lyon = SEIR(0.09*int(S0),0.0)
    villes.add_node(3, name="Lyon", epi=epi_lyon, cut=1.0)
    
    epi_toulouse = SEIR(0.085*int(S0),0.0)
    villes.add_node(4, name="Toulouse", epi=epi_toulouse, cut=1.0)
    
    epi_nice = SEIR(0.075*int(S0),0.0)
    villes.add_node(5, name="Nice", epi=epi_nice, cut=1.0)
    
    epi_nantes = SEIR(0.065*int(S0),0.0)
    villes.add_node(6, name="Nantes", epi=epi_nantes, cut=1.0)
    
    epi_monp = SEIR(0.05*int(S0),0.0)
    villes.add_node(7, name="Montpellier", epi=epi_monp, cut=1.0)
    
    epi_stras = SEIR(0.045*int(S0),0.0)
    villes.add_node(8, name="Strasbourg", epi=epi_stras, cut=1.0)
    
    epi_bordeaux = SEIR(0.045*int(S0),0.0)
    villes.add_node(9, name="Bordeaux", epi=epi_bordeaux, cut=1.0)
    
    epi_lille = SEIR(0.045*int(S0),0.0)
    villes.add_node(10, name="Lille", epi=epi_lille, cut=1.0)
    
    villes.add_edge(1, 2, weight=0.15 )
    villes.add_edge(1, 3, weight=0.18 )
    villes.add_edge(1, 9, weight=0.13 )
    villes.add_edge(1, 10, weight=0.11 )
    villes.add_edge(1, 8, weight=0.11 )
    villes.add_edge(1, 5, weight=0.09 )
    villes.add_edge(1, 6, weight=0.1 )
    villes.add_edge(1, 4, weight=0.08)
    villes.add_edge(1, 7, weight=0.05 )
    
    villes.add_edge(2, 1, weight=0.44)
    villes.add_edge(2, 3, weight=0.2)
    villes.add_edge(2, 5, weight=0.15)
    villes.add_edge(2, 7, weight=0.10)
    villes.add_edge(2, 8, weight=0.05)
    villes.add_edge(2, 10, weight=0.05)
      
    villes.add_edge(3, 1, weight=0.44)
    villes.add_edge(3, 2, weight=0.2)
    villes.add_edge(3, 5, weight=0.1)
    villes.add_edge(3, 7, weight=0.11)
    villes.add_edge(3, 8, weight=0.08)
    villes.add_edge(3, 10, weight=0.07)
    
    villes.add_edge(4, 9, weight=0.43)
    villes.add_edge(4, 1, weight=0.35)
    villes.add_edge(4, 6, weight=0.11)
    villes.add_edge(4, 7, weight=0.11)
    
    villes.add_edge(5, 2, weight=0.42)
    villes.add_edge(5, 1, weight=0.25)
    villes.add_edge(5, 10, weight=0.11)
    villes.add_edge(5, 7, weight=0.11)
    villes.add_edge(5, 3, weight=0.11)
    
    villes.add_edge(6, 1, weight=0.5)
    villes.add_edge(6, 9, weight=0.3)
    villes.add_edge(6, 8, weight=0.07)
    villes.add_edge(6, 10, weight=0.09)
    villes.add_edge(6, 4, weight=0.04)
    
    villes.add_edge(7, 1, weight=0.5)
    villes.add_edge(7, 4, weight=0.25)
    villes.add_edge(7, 9, weight=0.1)
    villes.add_edge(7, 8, weight=0.05)
    villes.add_edge(7, 2, weight=0.10)
    
    villes.add_edge(8, 1, weight=0.47)
    villes.add_edge(8, 3, weight=0.16)
    villes.add_edge(8, 2, weight=0.13)
    villes.add_edge(8, 10, weight=0.12)
    villes.add_edge(8, 6, weight=0.06)
    villes.add_edge(8, 9, weight=0.06)
    
    villes.add_edge(9, 1, weight=0.5)
    villes.add_edge(9, 6, weight=0.11)
    villes.add_edge(9, 4, weight=0.23)
    villes.add_edge(9, 8, weight=0.05)
    villes.add_edge(9, 10, weight=0.06)
    
    villes.add_edge(10, 1, weight=0.5)
    villes.add_edge(10, 2, weight=0.15)
    villes.add_edge(10, 3, weight=0.15)
    villes.add_edge(10, 6, weight=0.07)
    villes.add_edge(10, 8, weight=0.07)
    villes.add_edge(10, 5, weight=0.06)

    return villes

In [4]:
def SEIRgraph_model(S0="999",E0="1",beta=0.7,gamma=0.3,sigma=0.3,g1="0.001",g2="0.0005",\
                    smin="0.002",sc="0.01",smax="0.01",control=False, ft="200",\
                    icity="Paris",pcity="Paris",pday=0):
    
    V = construct_graph(S0,E0)
    R0 = beta/gamma
    i0 = 0
    fg1 =float(g1)
    fg2 = float(g2)
    for i in range(1,V.number_of_nodes()+1):
        V.nodes[i]['epi'].push_Rt(R0)
        if icity == V.nodes[i]['name']:
            i0 = i 
    V.nodes[i0]['epi'].E[-1]=int(E0)
    
    times = [0.0]
    dt = 0.2
    while times[-1]<int(ft):
        for i in range(1,V.number_of_nodes()+1):
            V.nodes[i]['epi'].push_list_to_n()
            V.nodes[i]['epi'].update(V.nodes[i]['epi'].xnp,V.nodes[i]['epi'].xn,\
                                          V.nodes[i]['epi'].xn,dt,beta,sigma,gamma)

        for i in range(1,V.number_of_nodes()+1):
            Sout =0.0
            Iout= 0.0
            Eout= 0.0
            Rout= 0.0
            for j in list(V.predecessors(i)):
                Sout = Sout + V[j][i]['weight']*V.nodes[j]['cut']*V.nodes[j]['epi'].xnp[0]
                Iout = Iout + V[j][i]['weight']*V.nodes[j]['cut']*V.nodes[j]['epi'].xnp[1]
                Eout = Eout + V[j][i]['weight']*V.nodes[j]['cut']*V.nodes[j]['epi'].xnp[2]
                Rout = Rout + V[j][i]['weight']*V.nodes[j]['cut']*V.nodes[j]['epi'].xnp[3]
   
            V.nodes[i]['epi'].xnp[0] = V.nodes[i]['epi'].xnp[0]+dt*fg1*(-V.nodes[i]['cut']*V.nodes[i]['epi'].xnp[0]+Sout)
            V.nodes[i]['epi'].xnp[1] = V.nodes[i]['epi'].xnp[1]+dt*fg1*(-V.nodes[i]['cut']*V.nodes[i]['epi'].xnp[1]+Eout)
            V.nodes[i]['epi'].xnp[2] = V.nodes[i]['epi'].xnp[2]+dt*fg2*(-V.nodes[i]['cut']*V.nodes[i]['epi'].xnp[2]+Iout)
            V.nodes[i]['epi'].xnp[3] = V.nodes[i]['epi'].xnp[3]+dt*fg2*(-V.nodes[i]['cut']*V.nodes[i]['epi'].xnp[3]+Rout)
            
            V.nodes[i]['epi'].push_np_to_list()
            V.nodes[i]['epi'].updateN()
            V.nodes[i]['epi'].push_Rt(R0)   
            
            for i in range(1,V.number_of_nodes()+1):
                if V.nodes[i]['epi'].I[-1]/V.nodes[i]['epi'].N[-1] < float(sc):
                    if control==True:
                        V.nodes[i]['cut']= 1.0
                else: 
                    if control==True:
                        V.nodes[i]['cut']= 0.0
  
        times.append(times[-1]+dt)  
        
    i0 = 0
    for i in range(1,V.number_of_nodes()+1):
        if pcity == V.nodes[i]['name']:
            i0 = i 
            
    plt.figure(figsize=(12,8))
    ax1 =plt.subplot(221)
    ax1.plot(times, V.nodes[i0]['epi'].N, 'r--', label=" Tot population") 
    ax1.plot(times, V.nodes[i0]['epi'].R, 'g--', label=" Recovered") 
    ax1.legend()

    ax2 =plt.subplot(222)
    un = np.ones(len(times))
    ax2.plot(times, V.nodes[i0]['epi'].Rt, 'c', label ="Rt")
    ax2.plot(times, un, 'r--')
    ax2.legend()
    
    ax3 = plt.subplot(223)  
    ax3.plot(times, V.nodes[i0]['epi'].S, label='suceptible')
    ax3.plot(times, V.nodes[i0]['epi'].E, label='exposed')
    ax3.plot(times, V.nodes[i0]['epi'].I, label='infected')  
    ax3.legend()
    
    color_map = []
    it = int(pday/dt)
    if it> len(times):
        it = len(times)-1
        
    for i in range(1,V.number_of_nodes()+1):
        if V.nodes[i]['epi'].I[it]/V.nodes[i]['epi'].N[it] < float(smin):
            color_map.append('green')
        elif V.nodes[i]['epi'].I[it]/V.nodes[i]['epi'].N[it] < float(smax):
            color_map.append('orange')
        else: 
            color_map.append('red')
    ax4 =  plt.subplot(224)
    labels = nx.get_node_attributes(V, 'name') 
    ax4 = nx.draw(V, labels=labels, node_color=color_map, font_weight='bold')
    plt.show()
    

## Numerical results for SEIR on graph

In [5]:
S0 = widgets.IntText(value=10000000,description="S0")
E0 = widgets.IntText(value=1,description="E0")
b1 = widgets.HBox([S0,E0])

beta = widgets.FloatSlider(value=0.7,min=0.01,max=1.0,step=0.02,description="beta")
gamma = widgets.FloatSlider(value=0.3,min=0.01,max=1.0,step=0.02,description="gamma")
sigma = widgets.FloatSlider(value=0.3,min=0.01,max=1.0,step=0.02,description="sigma")
b2 = widgets.HBox([beta,gamma,sigma])

g1 = widgets.FloatText(value=0.001,description="ratio pop travel")
g2 = widgets.FloatText(value=0.0005,description="ratio symptomatic travel")
b3 = widgets.HBox([g1,g2])

smin = widgets.FloatText(value=0.002,description="orange threshold")
sc = widgets.FloatText(value=0.01,description="stop travel threshold")
smax = widgets.FloatText(value=0.01,description="red travel threshold")
b4 = widgets.HBox([smin,sc,smax])

icity = widgets.Text(value='Paris',description="City for init epidemic")
pcity = widgets.Text(value="Paris",description="Plotted City data")
b5 = widgets.HBox([icity,pcity])

ft = widgets.IntText(value=200,description="Final time")
pday = widgets.IntSlider(value=0,min=0,max=200,step=1,description="Day for plot graph")

def boundpday(change):
        pday.max = change.new
    
ft.observe(boundpday, names='value')
b6 = widgets.HBox([ft,pday])

ui= widgets.VBox([b1,b2,b3,b4,b5,b6])
out = widgets.interactive_output(SEIRgraph_model, {'S0': S0, 'E0': E0, 'beta': beta, 'sigma': sigma, \
                                                'gamma': gamma, 'g1': g1, 'g2': g2, "smin":smin,\
                                                "sc": sc, "smax": smax, "icity": icity, "pcity": pcity,\
                                                "ft": ft, "pday": pday})


In [6]:
display(ui, out)

Output()